In [1]:
# Import Dependencies
import pandas as pd
import matplotlib.pyplot as plt
import scipy.stats as st
import numpy as np
import requests
import json
from pathlib import Path
from scipy import stats

In [2]:
# Store filepaths into variable
flight_data_csv = "Flight_on_time_HIX.csv"
cities = "airports.csv"

In [3]:
# Load Flight Data
flight_data_df = pd.read_csv(flight_data_csv)
flight_data_df.head()

Airline  Flight_Number Plane_ID FlightDate Origin_Airport  \
0      TR           4135   GJLOAB  12/1/2019            IYF   
1      TR           3776   GDISCI  12/1/2019            HEN   
2      RO           4754   GHHWLL  12/1/2019            HIX   
3      XM           5604   GBGWFC  12/1/2019            HIX   
4      XM           5612   GBISBC  12/1/2019            HIX   

  Destination_Airport  Flight_Distance  Scheduled_Departure_Time  \
0                 HIX              678                         1   
1                 HIX             1700                        10   
2                 IZN              413                        10   
3                 IZU              130                        10   
4                 LKF              258                        10   

   Actual_Departure_Time  Departure_Delay_Minutes  Departure_Taxi  \
0                    103                       62              15   
1                     25                       15              21   
2                     10                        0              15   
3                     44                       34              34   
4                    234                      144              26   

   Departure_WheelsOff  Scheduled_Arrival_Time  Actual_Arrival_Time  \
0                  118                     127                  219   
1                   46                     616                  624   
2                   25                     242                  227   
3                  118                     111                  155   
4                  300                     132                  358   

   Arrival_Delay_Minutes  Arrival_Taxi  Arrival_WheelsOn  Delay_Reason  
0                     52             7               212  LateAircraft  
1                      8            27               557           NaN  
2                      0             5               222           NaN  
3                     44             4               151       Weather  
4                    146             6               352       Carrier

In [4]:
cities_df = pd.read_csv(cities)
cities_df.head()

code       city                         airport           country
0  AAA       Anaa                            Anaa  French Polynesia
1  AAB   Arrabury                        Arrabury         Australia
2  AAC      Arish  El Arish International Airport             Egypt
3  AAD  Ad-Dabbah                       Ad-Dabbah             Sudan
4  AAE     Annaba                     Les Salines           Algeria

In [5]:
def find_city_name(row, column, df):
    value_to_find = row[column]
    matching_row = df[df['code'] == value_to_find]

    if not matching_row.empty:
        return matching_row['city'].values[0]
    else:
        return None


flight_data_df['origin_city'] = flight_data_df.apply(find_city_name, args=("Origin_Airport",cities_df), axis=1)

flight_data_df['destination_city'] = flight_data_df.apply(find_city_name, args=("Destination_Airport",cities_df), axis=1)


In [6]:
flight_data_df.head()

Airline  Flight_Number Plane_ID FlightDate Origin_Airport  \
0      TR           4135   GJLOAB  12/1/2019            IYF   
1      TR           3776   GDISCI  12/1/2019            HEN   
2      RO           4754   GHHWLL  12/1/2019            HIX   
3      XM           5604   GBGWFC  12/1/2019            HIX   
4      XM           5612   GBISBC  12/1/2019            HIX   

  Destination_Airport  Flight_Distance  Scheduled_Departure_Time  \
0                 HIX              678                         1   
1                 HIX             1700                        10   
2                 IZN              413                        10   
3                 IZU              130                        10   
4                 LKF              258                        10   

   Actual_Departure_Time  Departure_Delay_Minutes  Departure_Taxi  \
0                    103                       62              15   
1                     25                       15              21   
2                     10                        0              15   
3                     44                       34              34   
4                    234                      144              26   

   Departure_WheelsOff  Scheduled_Arrival_Time  Actual_Arrival_Time  \
0                  118                     127                  219   
1                   46                     616                  624   
2                   25                     242                  227   
3                  118                     111                  155   
4                  300                     132                  358   

   Arrival_Delay_Minutes  Arrival_Taxi  Arrival_WheelsOn  Delay_Reason  \
0                     52             7               212  LateAircraft   
1                      8            27               557           NaN   
2                      0             5               222           NaN   
3                     44             4               151       Weather   
4                    146             6               352       Carrier   

  origin_city destination_city  
0        None          Hiva Oa  
1      Hendon          Hiva Oa  
2     Hiva Oa             None  
3     Hiva Oa             None  
4     Hiva Oa             None

In [7]:
unique_cities = pd.unique(flight_data_df[['origin_city', 'destination_city']].values.ravel('K'))
adjusted_unique_cities = []

import re

def remove_parent(input_string):
    if input_string is None:
        return
    
    if '(' not in input_string and ')' not in input_string:
        return input_string  
    
    pattern = r'\(.*?\)\s*'
    result = re.sub(pattern, '', input_string)
    return result

for city in unique_cities:
    adjusted_unique_cities.append(remove_parent(city))

adjusted_unique_cities




[None,
 'Hendon',
 'Hiva Oa',
 'Tlemcen',
 'Erechim',
 'Errol ',
 'Lowai',
 'Liverpool',
 'Barreirinhas',
 'Red Lake',
 'Kuopio',
 'La Grange ',
 'Moma',
 'Fagernes',
 'Chile Chico',
 'Tasikmalaya',
 'Bennettsville ',
 'Benson',
 'Uliastai',
 'Milford ',
 'Maputo',
 'Kigoma',
 'Estevan',
 'Fort Smith ',
 'Lashio',
 'Moanda',
 'Fitiuta',
 'Cortes Bay',
 'Xichang',
 'Fairbury ',
 'Unguia',
 'Macmillan Pass',
 'Villa Dolores',
 'Errachidia',
 'Lublin',
 'Vitoria Da Conquista',
 'Truckee ',
 'Morelia',
 'Lago Argentino',
 'Tete',
 'Taskul',
 'Lawton ',
 'Termez',
 'Vredendal',
 'Angelholm, Helsingborg',
 'Londolozi',
 'Isles Of Scilly',
 'Ceres',
 'La Rochelle',
 'Manaung',
 'Fuyun',
 'Iraan ',
 'Funafuti Atol',
 'Bemichi',
 'Moses Lake ',
 'Vaeroy',
 'Seo De Urgel',
 'Barahona',
 'Viqueque',
 'Lichinga',
 'Tokushima',
 'Likiep Island',
 'Tenerife',
 'Lydd',
 'Vanuabalavu',
 'Laoag',
 'Wendover ',
 'Lake Charles ',
 'Cherribah',
 'Rivers Inlet',
 'Miandrivazo',
 'Karawari',
 'Charleston ',

In [8]:
def getCityCood(city):
    
    city_url = f"https://geocoding-api.open-meteo.com/v1/search?name={city}&count=10&language=en&format=json"

    city_lat_lon = requests.get(city_url).json()

    return {'lat': city_lat_lon['results'][0]['latitude'], 'lon': city_lat_lon['results'][0]['longitude']}


def getCityWeather(lat, lon):
    url = f'https://archive-api.open-meteo.com/v1/archive?latitude={lat}&longitude={lon}&start_date=2019-12-01&end_date=2019-12-31&hourly=temperature_2m,precipitation,cloudcover,windspeed_100m'

    city_weather = requests.get(url).json()

    return city_weather


def getWeather(city):

    try:
        params = getCityCood(city)
    except:
        print("error using the coord api")
        return
    try:
        cityWeather = getCityWeather(params['lat'], params['lon'])
    except:
        print("error using the weather api")

    return cityWeather

weatherInfo = {}

for city in adjusted_unique_cities:
    weatherInfo[city] = getWeather(city)

weatherInfo

error using the coord api
error using the coord api
error using the coord api
error using the coord api
error using the coord api


{None: {'latitude': 44.90001,
  'longitude': 7.5,
  'generationtime_ms': 0.2129077911376953,
  'utc_offset_seconds': 0,
  'timezone': 'GMT',
  'timezone_abbreviation': 'GMT',
  'elevation': 246.0,
  'hourly_units': {'time': 'iso8601',
   'temperature_2m': '°C',
   'precipitation': 'mm',
   'cloudcover': '%',
   'windspeed_100m': 'km/h'},
  'hourly': {'time': ['2019-12-01T00:00',
    '2019-12-01T01:00',
    '2019-12-01T02:00',
    '2019-12-01T03:00',
    '2019-12-01T04:00',
    '2019-12-01T05:00',
    '2019-12-01T06:00',
    '2019-12-01T07:00',
    '2019-12-01T08:00',
    '2019-12-01T09:00',
    '2019-12-01T10:00',
    '2019-12-01T11:00',
    '2019-12-01T12:00',
    '2019-12-01T13:00',
    '2019-12-01T14:00',
    '2019-12-01T15:00',
    '2019-12-01T16:00',
    '2019-12-01T17:00',
    '2019-12-01T18:00',
    '2019-12-01T19:00',
    '2019-12-01T20:00',
    '2019-12-01T21:00',
    '2019-12-01T22:00',
    '2019-12-01T23:00',
    '2019-12-02T00:00',
    '2019-12-02T01:00',
    '2019-12-02T02

In [9]:
weatherJsonPath = "utils/weather_info.json"

with open(weatherJsonPath, 'w') as jsonfile:
    json.dump(weatherInfo, jsonfile, default=str, indent=4)

In [57]:
from datetime import datetime

def get_hour_from_df(hourString):

    if len(hourString) > 2:
        if len(hourString) == 3:
            return "0" + hourString[-3]
        return hourString[-4] + hourString[-3]
    
    return '00'


def extract_hour(datetimeString):
    try:
        dt_obj = datetime.strptime(datetimeString, '%Y-%m-%dT%H:%M')
        
        hour_str = dt_obj.strftime('%H')
        
        return hour_str
    except ValueError:
        return None  
    
    
def normalize_date_format(date_str):
    try:
        if '/' in date_str:
            date_obj = datetime.strptime(date_str, '%m/%d/%Y')
        elif 'T' in date_str:
            date_obj = datetime.strptime(date_str, '%Y-%m-%dT%H:%M')
        else:
            return None  

        normalized_date_str = date_obj.strftime('%Y-%m-%d')
        return normalized_date_str
    except ValueError:
        return None 
    

def compare_dates(date_str1, date_str2):

    normalized_date_str1 = normalize_date_format(date_str1)
    normalized_date_str2 = normalize_date_format(date_str2)

    if normalized_date_str1 and normalized_date_str2:
        return normalized_date_str1 == normalized_date_str2
    else:
        return False

def find_item_position(my_array, item_to_find):
    position = None

    for i in range(len(my_array)):
        if my_array[i] == item_to_find:
            position = i
            break 

    return position   
    

def getTemperature(row, orig_dest_city, orig_dest_hour):

    date = row['FlightDate']
    city = row[orig_dest_city]
    hour = row[orig_dest_hour]

    try:

        for i in range(len(weatherInfo[city]['hourly']['time'])):
            
            if compare_dates(date, weatherInfo[city]['hourly']['time'][i]) and extract_hour(weatherInfo[city]['hourly']['time'][i]) == get_hour_from_df(str(hour)):
                
                return weatherInfo[city]['hourly']['temperature_2m'][i]
            
    except:
        print('failed')    
    
    return "item not found"





In [59]:
flight_data_df['temperature'] = flight_data_df.apply(getTemperature, args=("origin_city","Scheduled_Departure_Time"), axis=1)
flight_data_df.head()

failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed
failed

Airline  Flight_Number Plane_ID FlightDate Origin_Airport  \
0      TR           4135   GJLOAB  12/1/2019            IYF   
1      TR           3776   GDISCI  12/1/2019            HEN   
2      RO           4754   GHHWLL  12/1/2019            HIX   
3      XM           5604   GBGWFC  12/1/2019            HIX   
4      XM           5612   GBISBC  12/1/2019            HIX   

  Destination_Airport  Flight_Distance  Scheduled_Departure_Time  \
0                 HIX              678                         1   
1                 HIX             1700                        10   
2                 IZN              413                        10   
3                 IZU              130                        10   
4                 LKF              258                        10   

   Actual_Departure_Time  Departure_Delay_Minutes  ...  Departure_WheelsOff  \
0                    103                       62  ...                  118   
1                     25                       15  ...                   46   
2                     10                        0  ...                   25   
3                     44                       34  ...                  118   
4                    234                      144  ...                  300   

   Scheduled_Arrival_Time  Actual_Arrival_Time  Arrival_Delay_Minutes  \
0                     127                  219                     52   
1                     616                  624                      8   
2                     242                  227                      0   
3                     111                  155                     44   
4                     132                  358                    146   

   Arrival_Taxi  Arrival_WheelsOn  Delay_Reason origin_city destination_city  \
0             7               212  LateAircraft        None          Hiva Oa   
1            27               557           NaN      Hendon          Hiva Oa   
2             5               222           NaN     Hiva Oa             None   
3             4               151       Weather     Hiva Oa             None   
4             6               352       Carrier     Hiva Oa             None   

  temperature  
0         6.2  
1         2.9  
2        23.4  
3        23.4  
4        23.4  

[5 rows x 21 columns]

In [60]:
flight_data_df.head(20)

Airline  Flight_Number Plane_ID FlightDate Origin_Airport  \
0       TR           4135   GJLOAB  12/1/2019            IYF   
1       TR           3776   GDISCI  12/1/2019            HEN   
2       RO           4754   GHHWLL  12/1/2019            HIX   
3       XM           5604   GBGWFC  12/1/2019            HIX   
4       XM           5612   GBISBC  12/1/2019            HIX   
5       XM           5615   GBJODX  12/1/2019            HIX   
6       XM           5661   GBESAF  12/1/2019            HIX   
7       CA           6526   GCDTFM  12/1/2019            TLM   
8       CA           7201   GBDVFM  12/1/2019            UKP   
9       NR           3741   GDJRDD  12/1/2019            HIX   
10      NR           3535   GEKWHO  12/1/2019            HIX   
11      NR           2895   GGFVEG  12/1/2019            HIX   
12      SN           6159   GEENNK  12/1/2019            HIX   
13      SN           6143   GEJTNK  12/1/2019            HIX   
14      ZH           5902   GFHSTX  12/1/2019            HIX   
15      ZH           5822   GFDRTX  12/1/2019            HIX   
16      SN           5243   GEJNNK  12/1/2019            HIX   
17      SN           5190   GEETNK  12/1/2019            HIX   
18      SN           5187   GEJRNK  12/1/2019            HIX   
19      XM           5607   GBGOXF  12/1/2019            HIX   

   Destination_Airport  Flight_Distance  Scheduled_Departure_Time  \
0                  HIX              678                         1   
1                  HIX             1700                        10   
2                  IZN              413                        10   
3                  IZU              130                        10   
4                  LKF              258                        10   
5                  MPM              475                        10   
6                  EZN              552                        10   
7                  HIX              977                        10   
8                  HIX              763                        10   
9                  FJS              836                        10   
10                 LRN             1041                        10   
11                 UFM              867                        10   
12                 XMP              272                        10   
13                 VFO              315                        10   
14                 FJH              109                        10   
15                 VZX              196                        10   
16                 VNU              213                        10   
17                 TQI              122                        10   
18                 KJN              268                        10   
19                 KZW              642                        15   

    Actual_Departure_Time  Departure_Delay_Minutes  ...  Departure_WheelsOff  \
0                     103                       62  ...                  118   
1                      25                       15  ...                   46   
2                      10                        0  ...                   25   
3                      44                       34  ...                  118   
4                     234                      144  ...                  300   
5                     144                       94  ...                  155   
6                      14                        4  ...                   38   
7                      22                       12  ...                   40   
8                    2358                        0  ...                   22   
9                       3                        0  ...                   17   
10                     55                       45  ...                  106   
11                     29                       19  ...                   50   
12                    121                       71  ...                  138   
13                    236                      146  ...                  250   
14      